This notebook involves adding all features to all routes and seperating them out based on route and stop

In [1]:
#Import the required packages
import scipy
#Import package pandas for data analysis
import pandas as pd

#Import package numpy for numeric computing
import numpy as np

#Import package matplotlib for visualisation/plotting
import matplotlib.pyplot as plt

#Import package seaborn for visualisation
import seaborn as sns

#For showing plots directly in the notebook run the command below
%matplotlib inline

from matplotlib.backends.backend_pdf import PdfPages

from scipy import stats

#Import all prediction packages
import sqlalchemy
from sqlalchemy import create_engine
from pandas import pandas as pd
from sklearn.tree import DecisionTreeRegressor
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import f1_score
from sklearn.metrics import r2_score
from sklearn import tree
import matplotlib.pyplot as plt
import pickle
import requests
import json
import numpy as np
import datetime
import time
from time import gmtime
from time import strftime
from sklearn.metrics import mean_squared_error
import os
import xgboost


import warnings
warnings.filterwarnings('ignore')

In [7]:
df = pd.read_feather("MasterCleanedLeaving&TripsDataCombined.feather")

In [13]:
unique_routes = df.LINEID.unique()
print(unique_routes)

['1' '13' '37' '104' '11' '102' '151' '41' '65' '7A' '140' '84' '79A'
 '15A' '17' '44' '40B' '41C' '83A' '238' '25' '38A' '63' '4' '66A' '31'
 '150' '17A' '25B' '31A' '27B' '33' '32' '14' '67' '9' '61' '43' '130'
 '68' '15' '123' '122' '120' '47' '69' '39A' '76' '40' '70' '29A' '25A'
 '38' '49' '65B' '39' '45A' '42' '77A' '27' '54A' '46A' '27A' '40D' '7'
 '53' '33B' '75' '270' '18' '16' '41B' '145' '79' '16C' '66' '15B' '83'
 '185' '26' '56A' '33A' '59' '220' '184' '142' '31B' '68A' '66B' '111'
 '236' '84A' '67X' '84X' '239' '42D' '66X' '41X' '46E' '38B' '7B' '114'
 '7D' '32X' '44B' '33X' '25D' '51D' '15D' '31D' '39X' '27X' '51X' '76A'
 '25X' '77X' '38D' '69X' '41A' '14C' '70D' '116' '118' '161' '68X' '33D'
 '40E' '16D' '33E' '41D']


In [2]:
#Function to add feather files with all features for all routes

def segmentToCSV(route,direction):
    #read in feather file

    df_route = df.loc[df['LINEID'] == route]
#     print(df_route)
    df_route_direction = df_route.loc[df_route['DIRECTION'] == direction]
    df_route_direction = df_route_direction.sort_values(by=['TRIPID', 'DAYOFSERVICE','PROGRNUMBER'], ascending = [False,True,True])
    print('Line and Direction:',route, direction)
    df_route_features=add_features(df_route_direction)
    print('Added features for:',route, direction)
    df_route_weather= add_weather(df_route_features)
    print('Added weather for:',route, direction)
    unique_stops = df_route_weather.STOPPOINTID.unique()
#     df_route_weather.to_feather('wholeRoutesLeah/df_'+str(route)+'_' + str(direction)+'.feather')
    
    for stop in unique_stops:
        df_route_direction_stop = df_route_weather.loc[df_route_weather['STOPPOINTID'] == stop]
        df_route_direction_stop.to_csv('segmentsByStop/df_'+str(route)+'_' + str(direction)+'_'+str(stop)+'.csv')
        print(route, direction,stop,'Complete')
 

In [6]:
#get all routes and create feather files with all data for all routes in both directions

unique_routes = df.LINEID.unique()

    
for route in unique_routes:
    
    segmentToCSV(route,1)
    segmentToCSV(route,2)

Line and Direction: 1 1
Added features for: 1 1
Added weather for: 1 1
Line and Direction: 1 2
Added features for: 1 2
Added weather for: 1 2
Line and Direction: 13 1
Added features for: 13 1
Added weather for: 13 1
Line and Direction: 13 2
Added features for: 13 2
Added weather for: 13 2
Line and Direction: 37 1
Added features for: 37 1
Added weather for: 37 1
Line and Direction: 37 2
Added features for: 37 2
Added weather for: 37 2
Line and Direction: 104 1
Added features for: 104 1
Added weather for: 104 1
Line and Direction: 104 2
Added features for: 104 2
Added weather for: 104 2
Line and Direction: 11 1
Added features for: 11 1
Added weather for: 11 1
Line and Direction: 11 2
Added features for: 11 2
Added weather for: 11 2
Line and Direction: 102 1
Added features for: 102 1
Added weather for: 102 1
Line and Direction: 102 2
Added features for: 102 2
Added weather for: 102 2
Line and Direction: 151 1
Added features for: 151 1
Added weather for: 151 1
Line and Direction: 151 2
Add

OSError: [Errno 28] No space left on device

In [2]:
#get all stop csv names
def get_segmentsStops():

    segmentsStops = set()
    for name in os.listdir("segmentsByStop"):
#         match = re.match("(\w+)_(\d)\.feather", name)
#         if match is None:
#             print("Skipping: "  +name)
#         line, direction, stop = match.groups()
        segmentsStops.add((name))
        
    return segmentsStops

In [2]:
#get all routes feather names
def get_segments():

    segmentsStops = set()
    for name in os.listdir("wholeRoutesFullSet"):
#         match = re.match("(\w+)_(\d)\.feather", name)
#         if match is None:
#             print("Skipping: "  +name)
#         line, direction, stop = match.groups()
        segmentsStops.add((name))
        
    return segmentsStops

In [44]:
getWholeRoutes = get_segmentsStops()
getWholeRoutes.remove('.ipynb_checkpoints')
print(getWholeRoutes)

{'df_39X_2.feather', 'df_38D_2.feather', 'df_41X_2.feather', 'df_4_2.feather', 'df_47_1.feather', 'df_11_1.feather', 'df_40_1.feather', 'df_45A_2.feather', 'df_151_2.feather', 'df_104_1.feather', 'df_41D_1.feather', 'df_14_1.feather', 'df_111_2.feather', 'df_111_1.feather', 'df_38A_1.feather', 'df_61_2.feather', 'df_69X_1.feather', 'df_84_1.feather', 'df_9_1.feather', 'df_122_2.feather', 'df_43_1.feather', 'df_27X_2.feather', 'df_25X_2.feather', 'df_40B_2.feather', 'df_15B_1.feather', 'df_29A_1.feather', 'df_39A_1.feather', 'df_150_2.feather', 'df_33A_1.feather', 'df_47_2.feather', 'df_27_2.feather', 'df_41X_1.feather', 'df_9_2.feather', 'df_15B_2.feather', 'df_220_1.feather', 'df_25D_2.feather', 'df_70D_2.feather', 'df_66B_2.feather', 'df_84_2.feather', 'df_33X_2.feather', 'df_76A_2.feather', 'df_18_2.feather', 'df_39_2.feather', 'df_31B_2.feather', 'df_25_2.feather', 'df_7D_1.feather', 'df_270_2.feather', 'df_25_1.feather', 'df_70_2.feather', 'df_7B_1.feather', 'df_43_2.feather', 'df

In [70]:
allStops = get_segmentsStops()
allStops.remove('GeneralRouteStopTemplate.ipynb')
allStops.remove('.ipynb_checkpoints')
print(allStops)

{'df_16_2_320.csv', 'df_46A_2_2065.csv', 'df_16_1_5051.csv', 'df_46A_2_461.csv', 'df_46A_2_801.csv', 'df_46A_2_806.csv', 'df_16_1_1301.csv', 'df_16_1_1293.csv', 'df_46A_2_4569.csv', 'df_16_1_229.csv', 'df_16_1_52.csv', 'df_120_2_2809.csv', 'df_46A_1_808.csv', 'df_46A_2_769.csv', 'df_16_1_232.csv', 'df_120_2_408.csv', 'df_16_2_1625.csv', 'df_16_2_1348.csv', 'df_16_1_2969.csv', 'df_46A_2_2069.csv', 'df_16_1_1631.csv', 'df_16_1_7068.csv', 'df_46A_2_2046.csv', 'df_16_1_1295.csv', 'df_16_2_1325.csv', 'df_46A_2_802.csv', 'df_46A_2_907.csv', 'df_46A_1_847.csv', 'df_46A_1_767.csv', 'df_120_1_487.csv', 'df_46A_1_2007.csv', 'df_120_1_824.csv', 'df_46A_1_2008.csv', 'df_16_1_1303.csv', 'df_46A_1_4962.csv', 'df_46A_1_813.csv', 'df_46A_1_2032.csv', 'df_120_2_4935.csv', 'df_16_1_7603.csv', 'df_46A_1_761.csv', 'df_16_1_2970.csv', 'df_46A_1_334.csv', '16_120_46A_stop_metrics.csv', 'df_16_1_215.csv', 'df_46A_2_2040.csv', 'df_16_2_5171.csv', 'df_46A_1_2015.csv', 'df_16_2_7615.csv', 'df_16_1_1635.csv', 'd

In [3]:
#function to add all features

def add_features(data):
    dates = []
    for row in data['DAYOFSERVICE']:
        dates.append(row)
    priorstops = data['PROGRNUMBER']
    #creating the array of priorstops
    priorstops = np.array(priorstops[:-1]).astype(int)
    #Creating actual arrival time of prior stopid
    priorstops_actualTime_Arr = data['ACTUALTIME_ARR']
    priorstops_actualTime_Arr = np.array(priorstops_actualTime_Arr[:-1])
    priorstops_actualTime_Arr = np.insert(priorstops_actualTime_Arr, 0, priorstops_actualTime_Arr[0])
    data['priorstops_actualTime_Arr'] = priorstops_actualTime_Arr
    data['JourneyTime'] = data['ACTUALTIME_DEP'] - data['priorstops_actualTime_Arr']
    data['PROGRNUMBER']=data['PROGRNUMBER'].astype('int')
    planned_journey_times = np.zeros(len(data))
    planned_journey_times[1:]=data.PLANNEDTIME_DEP.values[1:]-data.PLANNEDTIME_ARR.values[:-1]
    data['planned_journey_time']=planned_journey_times
    data['delay']=data['JourneyTime']-planned_journey_times
    
    actualTime_Arr = []

    for row in data['ACTUALTIME_ARR']:
        time = strftime("%H:%M:%S", gmtime(row))
        actualTime_Arr.append(time)
    data['ACTUALTIME_ARR'] = actualTime_Arr
    
    actualTime_Dep = []

    for row in data['ACTUALTIME_DEP']:
        time = strftime("%H:%M:%S", gmtime(row))
        actualTime_Dep.append(time)
    data['ACTUALTIME_DEP'] = actualTime_Dep
    
    PlannedTime_Arr = []

    for row in data['PLANNEDTIME_ARR']:
        time = strftime("%H:%M:%S", gmtime(row))
        PlannedTime_Arr.append(time)
    data['PLANNEDTIME_ARR'] = PlannedTime_Arr
    
    PlannedTime_Dep = []

    for row in data['PLANNEDTIME_DEP']:
        time = strftime("%H:%M:%S", gmtime(row))
        PlannedTime_Dep.append(time)
        
    data['PLANNEDTIME_DEP'] = PlannedTime_Dep
    
    priorStopsActualTime_Arr = []

    for row in data['priorstops_actualTime_Arr']:
        time = strftime("%H:%M:%S", gmtime(row))
        priorStopsActualTime_Arr.append(time)
        
    data['priorstops_actualTime_Arr'] = priorStopsActualTime_Arr
    
    data['Month'] = data['DAYOFSERVICE'].dt.month
    data['Day'] = data['DAYOFSERVICE'].dt.dayofweek
    data['Hour'] = data['ACTUALTIME_ARR'].apply(pd.to_datetime).dt.hour
    
    
    list_School = []

    for row in data['Month']:
        if row == 6 or row == 7 or row== 8:
            list_School.append('0')
        else:
            list_School.append('1')  
    data['School']=list_School 
    
    list_rushHour = []

    for row in data['ACTUALTIME_DEP']:
        if row >= '07:00:00' and row <= '08:30:00' or row >= '16:00:00' and row <= '18:00:00':
            list_rushHour.append('1')
        else:
            list_rushHour.append('0')
            
    data['RushHour']=list_rushHour
    
    list_weekend = []

    for row in data['Day']:
        if row == '5' or row == '6':
            list_weekend.append('1')
        else:
            list_weekend.append('0')
    data['Weekend'] = list_weekend
    
    holidays = ['2018/01/01', '2018/03/17', '2018/04/02', '2018/05/07','2018/06/04', '2018/08/06', '2018/10/29', '2018/12/25', '2018/12/26']

    newHolidays = []
    for holiday in holidays:
        newHolidays.append(datetime.datetime.strptime(holiday,"%Y/%m/%d"))
    newhols1 = []

    for holiday in newHolidays:
          newhols1.append(holiday.date())
    
    list_dfHols = []
    for row in data['DAYOFSERVICE']:
    #         print(row.date())
        if row.date() == datetime.date(2018, 1, 1) or row.date() == datetime.date(2018, 3, 17) or row.date() == datetime.date(2018, 4, 2) or row.date() == datetime.date(2018, 5, 7) or row.date() == datetime.date(2018, 6, 4) or row.date() == datetime.date(2018, 8, 6) or row.date() == datetime.date(2018, 10, 29) or row.date() ==  datetime.date(2018, 12, 25) or row.date() == datetime.date(2018, 12, 26):
    #             print('true')
            list_dfHols.append('1')           
        else:
            list_dfHols.append('0')
    #             print('false')
    
    data['Holiday'] = list_dfHols
    data = data[(data['JourneyTime'] > 0)]
#     z = np.abs(stats.zscore(data['JourneyTime']))
#     data = data[(z < 2)]
    
    return data


In [4]:
#function to add all weather data

def add_weather(data):
    weather = pd.read_csv('historic_weather.csv')
    #Adding Hour and DayOfService Feature to the weather dataframe to be able to merge with the route 16 dataframe.
    weather['Hour'] = weather.weather_date.apply(pd.to_datetime).dt.hour
    weather['DAYOFSERVICE'] = weather.weather_date.apply(pd.to_datetime).dt.date
    weather['rain'] = weather['rain'].astype('float')
    weather['DAYOFSERVICE'] = weather['DAYOFSERVICE'].astype('datetime64[ns]')
    WeatherCombined_df = pd.merge(data,
                 weather,
                 on=['Hour', 'DAYOFSERVICE'])
    WeatherCombined_df = WeatherCombined_df.drop(columns = ['dewpt','vappr','rhum','msl','wddir','ww','w','sun','clht','clamt'])
    return WeatherCombined_df
    

In [5]:
#function to evaluate metrics

def evalMetrics(data):
    route_name = data.ROUTEID[0] 
    route_direction = data.DIRECTION[0]
    data = data[['STOPPOINTID','Month','Day','Hour','School','RushHour','Weekend','Holiday','rain','temp','wdsp','vis','delay']]
    
    linearModel = LinearRegression()
    decisionTree = DecisionTreeRegressor(max_depth=25, max_leaf_nodes = 206000)
#     randForestModel = RandomForestRegressor(n_estimators = 3, random_state=10, max_depth = 25, max_leaf_nodes = 206000)
# #     XGBoost = xgboost.XGBClassifier()
    
    models= [('lin_reg', linearModel), ('decision Tree', decisionTree)]
    
    z = np.abs(stats.zscore(data['delay']))
    data_no_outliers = data[(z < 3)]
    
#     y=data["JourneyTime"]
    y=data["delay"]
    X=data.drop(['delay'],axis=1)
    
    X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.2,random_state=1)
    
    linearModel.fit(X_train,y_train)
    decisionTree.fit(X_train, y_train)
#     randForestModel.fit(X_train, y_train.values.ravel())
#     pickle.dump(linearModel, open(f'wholeRouteLinearPklFull/linearModelWhole'+'_'+str(route_name)+'_'+str(route_direction)+'.pkl','wb'))
#     pickle.dump(decisionTree, open(f'wholeRouteDecisionTreePklFull/decisionTreeModelWhole'+'_'+str(route_name)+'_'+str(route_direction)+'.pkl','wb'))
# # #     XGBoost.fit(X_train,y_train)
    
    for i, model in models:    
        predictions = model.predict(X_train)
        MSE = mean_squared_error(y_train, predictions)
        RMSE = np.sqrt(MSE)
        msg = "%s = %.2f" % (i, round(RMSE, 2))
#         print('RMSE of', msg)
    
    for i, model in models:
        # Make predictions on train data
        predictions = model.predict(X_train)
        # Performance metrics
        errors = np.mean(abs(predictions - y_train))
        # Calculate mean absolute percentage error (MAPE)
#         mape = np.mean(100 * (errors / y_train))
        mape = np.mean(100 * (errors / y_train))
        # Calculate and display accuracy
        accuracy = 100 - mape    
        #print result
        msg = "%s= %.2f"% (i, round(accuracy, 2))
#         print('Performance of', msg,'%')
        print('MAE:', i,errors)



In [13]:
#function to add metrics to df

def metricsToDF(data):
    
    route_name = data.LINEID[0]
    route_direction=data.DIRECTION[0]
    stop_name = data.STOPPOINTID[0]
    
    linearModel = LinearRegression()
    decisionTree = DecisionTreeRegressor(max_depth=25, max_leaf_nodes = 206000)
    randForestModel = RandomForestRegressor(n_estimators = 3,random_state=10, max_depth = 25, max_leaf_nodes = 206000)
#     XGBoost = xgboost.XGBClassifier()
    
    models= [('lin_reg', linearModel),('decision Tree', decisionTree), ('random forest', randForestModel)]
    
    data = data.drop(["index","ArrDel","DepDel","Waiting_Time", "DAYOFSERVICE",'PROGRNUMBER','TRIPID', 'LINEID', 'weather_date','priorstops_actualTime_Arr','PLANNEDTIME_ARR', 'PLANNEDTIME_DEP','ACTUALTIME_ARR','ACTUALTIME_DEP', 'VEHICLEID', 'DAYOFSERVICE', 'ROUTEID', 'DIRECTION', 'wetb', 'planned_journey_time','JourneyTime'],axis=1)

    
#     y=data["JourneyTime"]
    y=data["delay"]
    X=data.drop(['delay'],axis=1)
#     print(X)
    
    X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.2,random_state=1)
    
    linearModel.fit(X_train,y_train)
    decisionTree.fit(X_train, y_train)
    randForestModel.fit(X_train, y_train.values.ravel())
#     XGBoost.fit(X_train,y_train)
    
    mape_list = []
    performance_list = []
    rmse_list = []
    model_list = []
    errors_list = []
    
    for i, model in models:    
        predictions = model.predict(X_train)
        MSE = mean_squared_error(y_train, predictions)
        RMSE = np.sqrt(MSE)
        model_list.append(i)
        rmse_list.append(RMSE)

          
    
    for i, model in models:
        predictions = model.predict(X_train)
        errors = np.mean(abs(predictions - y_train))
        errors_list.append(errors)

        
    data = {'Route':route_name,'Direction':route_direction,'Stop':stop_name,'Model':model_list,'RMSE': rmse_list,'MAE':errors_list}
    df = pd.DataFrame(data)
    print(df)
    return df



In [8]:
def getMaxMin(data):
    
    
    route_name = data.LINEID[0]
    print(route_name)
    route_direction=data.DIRECTION[0]
    stop_name = data.STOPPOINTID[0]
    
   
    max_value = data['delay'].max()
    min_value = data['delay'].min()
    print(max_value)
    print(min_value)
    
    
        
    data_new = {'Route':route_name,'Direction':route_direction,'Stop':stop_name,'Max': max_value,'Min':min_value}
    df = pd.DataFrame(data_new,index=[0])
    print(df)
    return df


In [12]:
#get full route metrics

allRoutes = get_segments()
allRoutes.remove('.ipynb_checkpoints')

all_dfs = []
for route in allRoutes:
    try:
        data = pd.read_feather('wholeRoutesFullSet/'+route)
    #         print('Evaluation Metrics for:' , stop)
    #         evalMetrics(data)
    #         print(stop)
        df_metrics = metricsToDF(data)
 
        all_dfs.append(df_metrics)
    #     print(x)
    except KeyError:
        pass
    except ValueError:
        pass
        
result = pd.concat(all_dfs)
result.to_csv('fullRouteMetrics.csv')
    


NameError: name 'get_segments' is not defined

In [22]:
#get stop metrics

allStops = get_segmentsStops()
allStops.remove('.ipynb_checkpoints')
print(allStops)

all_dfs = []
for stop in allStops:
    print(stop)
    try:
        data = pd.read_csv('segmentsByStop/'+stop)
    #         print('Evaluation Metrics for:' , stop)
    #         evalMetrics(data)
    #         print(stop)
        df_metrics = metricsToDF(data)
        all_dfs.append(df_metrics)
    #     print(x)
    except KeyError:
        pass
    except ValueError:
        pass
        
result = pd.concat(all_dfs)
result.to_csv('modelPerStopMetrics.csv')

{'df_66A_2_3373.csv', 'df_67_1_7075.csv', 'df_40D_2_7073.csv', 'df_67X_2_3928.csv', 'df_7D_2_3203.csv', 'df_31B_1_546.csv', 'df_63_1_2047.csv', 'df_17_2_3011.csv', 'df_25_2_2231.csv', 'df_4_1_39.csv', 'df_7_1_3041.csv', 'df_84_2_4148.csv', 'df_9_1_1285.csv', 'df_40B_2_7022.csv', 'df_31D_2_1188.csv', 'df_220_1_4364.csv', 'df_16C_1_219.csv', 'df_69X_1_3441.csv', 'df_40D_2_7097.csv', 'df_65_1_4007.csv', 'df_32X_2_496.csv', 'df_77A_2_2568.csv', 'df_7B_2_7419.csv', 'df_14_2_2847.csv', 'df_31A_1_710.csv', 'df_236_2_4321.csv', 'df_32X_1_3588.csv', 'df_69_2_4672.csv', 'df_102_1_6015.csv', 'df_79_1_2909.csv', 'df_14_2_2998.csv', 'df_67_2_2251.csv', 'df_66B_1_2191.csv', 'df_66_1_2198.csv', 'df_43_2_665.csv', 'df_65B_2_1158.csv', 'df_66_1_7391.csv', 'df_33B_1_3726.csv', 'df_68_1_1278.csv', 'df_122_2_12.csv', 'df_37_1_783.csv', 'df_44_1_209.csv', 'df_32X_1_3641.csv', 'df_40_2_1596.csv', 'df_43_1_3649.csv', 'df_27B_2_247.csv', 'df_40_1_1525.csv', 'df_40B_1_1509.csv', 'df_33E_1_3786.csv', 'df_25A_2_

   Route  Direction  Stop          Model       RMSE       MAE
0     67          1  7075        lin_reg  13.586329  9.706592
1     67          1  7075  decision Tree   4.195724  1.517736
2     67          1  7075  random forest   8.286044  5.070231
df_40D_2_7073.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   40D          2  7073        lin_reg  96.274466  50.124539
1   40D          2  7073  decision Tree   0.000000   0.000000
2   40D          2  7073  random forest  58.676543  24.071333
df_67X_2_3928.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   67X          2  3928        lin_reg  34.277271  21.526225
1   67X          2  3928  decision Tree   0.328230   0.027624
2   67X          2  3928  random forest  16.699054   9.639656
df_7D_2_3203.csv
  Route  Direction  Stop          Model       RMSE        MAE
0    7D          2  3203        lin_reg  17.774912  13.828310
1    7D          2  3203  decision Tree   0.000000   0.000000
2    7D          

  Route  Direction  Stop          Model       RMSE        MAE
0   66B          1  2191        lin_reg  31.278795  23.475241
1   66B          1  2191  decision Tree   2.331037   0.315579
2   66B          1  2191  random forest  17.143898  10.358873
df_66_1_2198.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     66          1  2198        lin_reg  18.910410  14.414718
1     66          1  2198  decision Tree   3.553429   0.857185
2     66          1  2198  random forest  10.587912   6.689299
df_43_2_665.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     43          2   665        lin_reg  26.215451  16.888084
1     43          2   665  decision Tree   5.628752   1.713324
2     43          2   665  random forest  14.363448   8.415563
df_65B_2_1158.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   65B          2  1158        lin_reg  28.936734  21.504325
1   65B          2  1158  decision Tree   9.853908   3.660680
2   65B    

   Route  Direction  Stop          Model       RMSE        MAE
0     63          2  2023        lin_reg  50.931506  36.928953
1     63          2  2023  decision Tree  13.968441   4.857643
2     63          2  2023  random forest  30.246765  18.492242
df_75_1_4342.csv
   Route  Direction  Stop          Model          RMSE           MAE
0     75          1  4342        lin_reg  3.082675e-12  2.984279e-12
1     75          1  4342  decision Tree  0.000000e+00  0.000000e+00
2     75          1  4342  random forest  5.574909e+02  5.436667e+02
df_39_1_1665.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     39          1  1665        lin_reg  27.604840  20.952822
1     39          1  1665  decision Tree  10.542700   4.070643
2     39          1  1665  random forest  16.829061  10.520904
df_29A_1_4472.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   29A          1  4472        lin_reg  17.054779  12.724230
1   29A          1  4472  decision Tree   3.

   Route  Direction  Stop          Model       RMSE        MAE
0     44          1  6097        lin_reg  18.359870  11.890591
1     44          1  6097  decision Tree   2.305467   0.551885
2     44          1  6097  random forest   9.950800   5.235283
df_69_1_1444.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     69          1  1444        lin_reg  48.955901  27.191802
1     69          1  1444  decision Tree   2.293379   0.285650
2     69          1  1444  random forest  30.155918  12.640533
df_39_1_1813.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     39          1  1813        lin_reg  91.047782  51.879302
1     39          1  1813  decision Tree  16.892921   6.155506
2     39          1  1813  random forest  48.302362  24.430692
df_39_2_1895.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     39          2  1895        lin_reg  15.248173  11.840160
1     39          2  1895  decision Tree   4.034365   1.219310
2   

...

  Route  Direction  Stop          Model      RMSE       MAE
0   45A          2  7056        lin_reg  9.901876  7.522537
1   45A          2  7056  decision Tree  1.815479  0.436596
2   45A          2  7056  random forest  5.948331  3.541650
df_33_2_3846.csv
   Route  Direction  Stop          Model       RMSE       MAE
0     33          2  3846        lin_reg  10.643058  7.843834
1     33          2  3846  decision Tree   1.808667  0.529202
2     33          2  3846  random forest   5.944421  3.481097
df_7A_2_3230.csv
  Route  Direction  Stop          Model       RMSE        MAE
0    7A          2  3230        lin_reg  22.612099  14.641558
1    7A          2  3230  decision Tree   4.078520   1.088804
2    7A          2  3230  random forest  13.904913   7.651798
df_51X_2_2142.csv
  Route  Direction  Stop          Model      RMSE       MAE
0   51X          2  2142        lin_reg  9.283901  7.443195
1   51X          2  2142  decision Tree  0.000000  0.000000
2   51X          2  2142  random

  Route  Direction  Stop          Model       RMSE        MAE
0   54A          2  2442        lin_reg  43.180035  29.720642
1   54A          2  2442  decision Tree  11.738339   4.165591
2   54A          2  2442  random forest  27.601321  16.620002
df_65B_1_7331.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   65B          1  7331        lin_reg  15.896578  11.637152
1   65B          1  7331  decision Tree   2.088789   0.351664
2   65B          1  7331  random forest   9.287866   5.767167
df_66X_1_780.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   66X          1   780        lin_reg  15.814913  12.361863
1   66X          1   780  decision Tree   0.000000   0.000000
2   66X          1   780  random forest   8.523967   5.154674
df_31_1_523.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     31          1   523        lin_reg  24.983535  14.922149
1     31          1   523  decision Tree   3.649612   1.017598
2     31        

   Route  Direction  Stop          Model       RMSE        MAE
0     84          2  3161        lin_reg  29.357881  21.872971
1     84          2  3161  decision Tree   7.172702   1.934127
2     84          2  3161  random forest  17.188401  10.350399
df_145_1_4173.csv
   Route  Direction  Stop          Model       RMSE        MAE
0    145          1  4173        lin_reg  25.606012  20.113137
1    145          1  4173  decision Tree  11.447392   5.221529
2    145          1  4173  random forest  16.525499  11.117636
df_38D_2_819.csv
  Route  Direction  Stop          Model       RMSE        MAE
0   38D          2   819        lin_reg  34.947471  28.515377
1   38D          2   819  decision Tree   0.000000   0.000000
2   38D          2   819  random forest  22.212359  13.020000
df_14_1_1195.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     14          1  1195        lin_reg  30.190577  18.886760
1     14          1  1195  decision Tree   6.255574   2.014381
2     1

   Route  Direction  Stop          Model       RMSE        MAE
0     13          1    37        lin_reg  47.975445  31.894852
1     13          1    37  decision Tree   6.400426   1.599056
2     13          1    37  random forest  28.566594  15.030723
df_13_1_2139.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     13          1  2139        lin_reg  13.489383  10.299429
1     13          1  2139  decision Tree   3.833078   1.157955
2     13          1  2139  random forest   8.311070   5.133627
df_33_1_3795.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     33          1  3795        lin_reg  30.949120  19.473879
1     33          1  3795  decision Tree   0.617635   0.072194
2     33          1  3795  random forest  15.442294   8.428612
df_68_2_1385.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     68          2  1385        lin_reg  38.744367  26.444027
1     68          2  1385  decision Tree   2.085578   0.369439
2   

   Route  Direction  Stop          Model       RMSE        MAE
0     44          1   853        lin_reg  53.945136  38.188558
1     44          1   853  decision Tree   1.812870   0.210978
2     44          1   853  random forest  28.046091  16.297669
df_15_2_1168.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     15          2  1168        lin_reg  27.321707  21.410522
1     15          2  1168  decision Tree  10.354364   4.149377
2     15          2  1168  random forest  17.734608  11.863281
df_220_1_7343.csv
   Route  Direction  Stop          Model       RMSE        MAE
0    220          1  7343        lin_reg  32.843666  18.610264
1    220          1  7343  decision Tree   1.712132   0.244914
2    220          1  7343  random forest  19.159891   9.348573
df_31_1_289.csv
   Route  Direction  Stop          Model       RMSE        MAE
0     31          1   289        lin_reg  73.654596  49.803138
1     31          1   289  decision Tree  11.708530   2.740945
2   

In [10]:
allStops = get_segmentsStops()
allStops.remove('.ipynb_checkpoints')
print(allStops)

all_dfs = []
for stop in allStops:
    print(stop)
  
    data = pd.read_csv('segmentsByStop/'+stop)     
    df = getMaxMin(data)
    all_dfs.append(df)
    
        
result = pd.concat(all_dfs)
result.to_csv('maxMinValuesOfStops.csv')

{'df_61_1_1035.csv', 'df_70D_2_3340.csv', 'df_65B_1_1079.csv', 'df_49_1_4878.csv', 'df_111_1_3052.csv', 'df_84X_2_4295.csv', 'df_32X_2_770.csv', 'df_220_2_1587.csv', 'df_25A_1_4562.csv', 'df_38D_1_7167.csv', 'df_51D_1_2141.csv', 'df_41D_2_49.csv', 'df_83_2_1071.csv', 'df_27_2_3952.csv', 'df_32X_2_3622.csv', 'df_63_1_3126.csv', 'df_75_1_4712.csv', 'df_151_1_7514.csv', 'df_140_2_6366.csv', 'df_236_2_7102.csv', 'df_7A_1_3217.csv', 'df_27_2_1269.csv', 'df_84X_2_2060.csv', 'df_56A_1_2102.csv', 'df_61_1_843.csv', 'df_140_1_6059.csv', 'df_239_2_6073.csv', 'df_41X_2_333.csv', 'df_79_2_5134.csv', 'df_111_1_3230.csv', 'df_65_2_7253.csv', 'df_145_2_4202.csv', 'df_77A_1_7460.csv', 'df_142_1_7196.csv', 'df_69_1_4720.csv', 'df_18_1_779.csv', 'df_18_1_2800.csv', 'df_75_1_2019.csv', 'df_83A_1_2480.csv', 'df_145_2_2993.csv', 'df_120_1_4934.csv', 'df_16_2_1328.csv', 'df_79_1_4407.csv', 'df_7D_2_3227.csv', 'df_41C_2_4907.csv', 'df_84X_2_4296.csv', 'df_33E_1_3756.csv', 'df_38_2_1697.csv', 'df_84A_1_4129.c

65B
479.0
-62.0
  Route  Direction  Stop    Max   Min
0   65B          1  1079  479.0 -62.0
df_49_1_4878.csv
49
299.0
-45.0
   Route  Direction  Stop    Max   Min
0     49          1  4878  299.0 -45.0
df_111_1_3052.csv
111
722.0
-804.0
   Route  Direction  Stop    Max    Min
0    111          1  3052  722.0 -804.0
df_84X_2_4295.csv
84X
702.0
-243.0
  Route  Direction  Stop    Max    Min
0   84X          2  4295  702.0 -243.0
df_32X_2_770.csv
32X
129.0
-88.0
  Route  Direction  Stop    Max   Min
0   32X          2   770  129.0 -88.0
df_220_2_1587.csv
220
453.0
-19.0
   Route  Direction  Stop    Max   Min
0    220          2  1587  453.0 -19.0
df_25A_1_4562.csv
25A
349.0
-34.0
  Route  Direction  Stop    Max   Min
0   25A          1  4562  349.0 -34.0
df_38D_1_7167.csv
38D
143.0
-28.0
  Route  Direction  Stop    Max   Min
0   38D          1  7167  143.0 -28.0
df_51D_1_2141.csv
51D
98.0
-16.0
  Route  Direction  Stop   Max   Min
0   51D          1  2141  98.0 -16.0
df_41D_2_49.csv
41D
16

0     40          1  1532  191.0 -30.0
df_27A_2_667.csv
27A
407.0
-331.0
  Route  Direction  Stop    Max    Min
0   27A          2   667  407.0 -331.0
df_54A_1_2395.csv
54A
362.0
-59.0
  Route  Direction  Stop    Max   Min
0   54A          1  2395  362.0 -59.0
df_14C_1_250.csv
14C
123.0
-70.0
  Route  Direction  Stop    Max   Min
0   14C          1   250  123.0 -70.0
df_65_2_4101.csv
65
236.0
-41.0
   Route  Direction  Stop    Max   Min
0     65          2  4101  236.0 -41.0
df_42_2_1221.csv
42
206.0
-90.0
   Route  Direction  Stop    Max   Min
0     42          2  1221  206.0 -90.0
df_41_2_3690.csv
41
646.0
-298.0
   Route  Direction  Stop    Max    Min
0     41          2  3690  646.0 -298.0
df_7D_1_4567.csv
7D
121.0
-40.0
  Route  Direction  Stop    Max   Min
0    7D          1  4567  121.0 -40.0
df_47_1_2075.csv
47
23.0
-33.0
   Route  Direction  Stop   Max   Min
0     47          1  2075  23.0 -33.0
df_69_1_4665.csv
69
481.0
-61.0
   Route  Direction  Stop    Max   Min
0     69   

46A
1690.0
-663.0
  Route  Direction  Stop     Max    Min
0   46A          2  4727  1690.0 -663.0
df_76_2_2120.csv
76
627.0
-60.0
   Route  Direction  Stop    Max   Min
0     76          2  2120  627.0 -60.0
df_45A_1_4147.csv
45A
271.0
-56.0
  Route  Direction  Stop    Max   Min
0   45A          1  4147  271.0 -56.0
df_39X_1_793.csv
39X
744.0
-236.0
  Route  Direction  Stop    Max    Min
0   39X          1   793  744.0 -236.0
df_31B_1_522.csv
31B
133.0
-45.0
  Route  Direction  Stop    Max   Min
0   31B          1   522  133.0 -45.0
df_44_2_4116.csv
44
200.0
-45.0
   Route  Direction  Stop    Max   Min
0     44          2  4116  200.0 -45.0
df_4_2_489.csv
4
1867.0
-72.0
   Route  Direction  Stop     Max   Min
0      4          2   489  1867.0 -72.0
df_84_2_4300.csv
84
315.0
-97.0
   Route  Direction  Stop    Max   Min
0     84          2  4300  315.0 -97.0
df_41D_1_3670.csv
41D
68.0
11.0
  Route  Direction  Stop   Max   Min
0   41D          1  3670  68.0  11.0
df_37_2_1689.csv
37
451.0

68A
896.0
-25.0
  Route  Direction  Stop    Max   Min
0   68A          1  1370  896.0 -25.0
df_44B_2_3517.csv
44B
288.0
-44.0
  Route  Direction  Stop    Max   Min
0   44B          2  3517  288.0 -44.0
df_41X_1_4915.csv
41X
155.0
-18.0
  Route  Direction  Stop    Max   Min
0   41X          1  4915  155.0 -18.0
df_68_2_1380.csv
68
234.0
-90.0
   Route  Direction  Stop    Max   Min
0     68          2  1380  234.0 -90.0
df_150_2_1111.csv
150
260.0
-233.0
   Route  Direction  Stop    Max    Min
0    150          2  1111  260.0 -233.0
df_38_2_7342.csv
38
251.0
-94.0
   Route  Direction  Stop    Max   Min
0     38          2  7342  251.0 -94.0
df_76A_2_2110.csv
76A
200.0
-148.0
  Route  Direction  Stop    Max    Min
0   76A          2  2110  200.0 -148.0
df_67X_1_318.csv
67X
190.0
-579.0
  Route  Direction  Stop    Max    Min
0   67X          1   318  190.0 -579.0
df_31D_1_913.csv
31D
204.0
-143.0
  Route  Direction  Stop    Max    Min
0   31D          1   913  204.0 -143.0
df_118_2_2069.cs

...

69
161.0
-188.0
   Route  Direction  Stop    Max    Min
0     69          1  5123  161.0 -188.0
df_54A_1_2391.csv
54A
346.0
-988.0
  Route  Direction  Stop    Max    Min
0   54A          1  2391  346.0 -988.0
df_7_2_480.csv
7
624.0
-93.0
   Route  Direction  Stop    Max   Min
0      7          2   480  624.0 -93.0
df_26_1_2210.csv
26
2052.0
-456.0
   Route  Direction  Stop     Max    Min
0     26          1  2210  2052.0 -456.0
df_77A_1_4347.csv
77A
607.0
-381.0
  Route  Direction  Stop    Max    Min
0   77A          1  4347  607.0 -381.0
df_14_2_3000.csv
14
529.0
-151.0
   Route  Direction  Stop    Max    Min
0     14          2  3000  529.0 -151.0
df_65_2_1358.csv
65
844.0
-57.0
   Route  Direction  Stop    Max   Min
0     65          2  1358  844.0 -57.0
df_43_2_675.csv
43
309.0
-63.0
   Route  Direction  Stop    Max   Min
0     43          2   675  309.0 -63.0
df_75_1_2542.csv
75
494.0
-38.0
   Route  Direction  Stop    Max   Min
0     75          1  2542  494.0 -38.0
df_66B_1_3954

41
829.0
-157.0
   Route  Direction  Stop    Max    Min
0     41          1   220  829.0 -157.0
df_70D_2_3352.csv
70D
59.0
-60.0
  Route  Direction  Stop   Max   Min
0   70D          2  3352  59.0 -60.0
df_49_2_1163.csv
49
668.0
-185.0
   Route  Direction  Stop    Max    Min
0     49          2  1163  668.0 -185.0
df_69_1_1449.csv
69
1436.0
-142.0
   Route  Direction  Stop     Max    Min
0     69          1  1449  1436.0 -142.0
df_29A_1_925.csv
29A
1031.0
-72.0
  Route  Direction  Stop     Max   Min
0   29A          1   925  1031.0 -72.0
df_66A_2_3373.csv
66A
1038.0
-139.0
  Route  Direction  Stop     Max    Min
0   66A          2  3373  1038.0 -139.0
df_151_2_2379.csv
151
213.0
-80.0
   Route  Direction  Stop    Max   Min
0    151          2  2379  213.0 -80.0
df_39_1_1648.csv
39
1563.0
-64.0
   Route  Direction  Stop     Max   Min
0     39          1  1648  1563.0 -64.0
df_38B_2_78.csv
38B
1441.0
-115.0
  Route  Direction  Stop     Max    Min
0   38B          2    78  1441.0 -115.0
d

145
2280.0
-1049.0
   Route  Direction  Stop     Max     Min
0    145          2  3146  2280.0 -1049.0
df_17A_1_138.csv
17A
207.0
-237.0
  Route  Direction  Stop    Max    Min
0   17A          1   138  207.0 -237.0
df_123_1_2185.csv
123
437.0
-201.0
   Route  Direction  Stop    Max    Min
0    123          1  2185  437.0 -201.0
df_49_1_7123.csv
49
943.0
-101.0
   Route  Direction  Stop    Max    Min
0     49          1  7123  943.0 -101.0
df_66B_2_2242.csv
66B
190.0
-73.0
  Route  Direction  Stop    Max   Min
0   66B          2  2242  190.0 -73.0
df_65_2_1163.csv
65
472.0
-192.0
   Route  Direction  Stop    Max    Min
0     65          2  1163  472.0 -192.0
df_33A_2_3846.csv
33A
86.0
-19.0
  Route  Direction  Stop   Max   Min
0   33A          2  3846  86.0 -19.0
df_67_1_3899.csv
67
2509.0
-40.0
   Route  Direction  Stop     Max   Min
0     67          1  3899  2509.0 -40.0
df_41X_1_6033.csv
41X
201.0
-45.0
  Route  Direction  Stop    Max   Min
0   41X          1  6033  201.0 -45.0
df_1

67X
207.0
-32.0
  Route  Direction  Stop    Max   Min
0   67X          2  3945  207.0 -32.0
df_33X_1_3777.csv
33X
167.0
-2.0
  Route  Direction  Stop    Max  Min
0   33X          1  3777  167.0 -2.0
df_25_2_2232.csv
25
296.0
-123.0
   Route  Direction  Stop    Max    Min
0     25          2  2232  296.0 -123.0
df_67_2_3926.csv
67
2345.0
-126.0
   Route  Direction  Stop     Max    Min
0     67          2  3926  2345.0 -126.0
df_16D_1_1285.csv
16D
310.0
-34.0
  Route  Direction  Stop    Max   Min
0   16D          1  1285  310.0 -34.0
df_56A_2_2778.csv
56A
415.0
-220.0
  Route  Direction  Stop    Max    Min
0   56A          2  2778  415.0 -220.0
df_67_1_2200.csv
67
257.0
-24.0
   Route  Direction  Stop    Max   Min
0     67          1  2200  257.0 -24.0
df_54A_2_2404.csv
54A
541.0
-110.0
  Route  Direction  Stop    Max    Min
0   54A          2  2404  541.0 -110.0
df_7D_2_2089.csv
7D
39.0
-9.0
  Route  Direction  Stop   Max  Min
0    7D          2  2089  39.0 -9.0
df_44B_1_2825.csv
44B
15

18
1367.0
-66.0
   Route  Direction  Stop     Max   Min
0     18          2  2780  1367.0 -66.0
df_33_2_3837.csv
33
427.0
-43.0
   Route  Direction  Stop    Max   Min
0     33          2  3837  427.0 -43.0


In [26]:
df.dtypes

STOPPOINTID      int64
delay          float64
Month            int64
Day              int64
Hour             int64
School           int64
RushHour         int64
Weekend          int64
Holiday          int64
rain           float64
temp           float64
wdsp             int64
vis              int64
clamt            int64
dtype: object